In [2]:
from bs4 import BeautifulSoup
import requests
import time, os

In [3]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys

chromedriver = "/home/aziker/WebDriver/chromedriver"
os.environ["webdriver.chrome.driver"] = chromedriver

In [10]:
driver = webdriver.Chrome(chromedriver)

In [11]:
#player name and transfer values
driver.get('https://www.transfermarkt.us/spieler-statistik/wertvollstespieler/marktwertetop')

In [12]:
soup = BeautifulSoup(driver.page_source, 'html.parser')

In [13]:
#testing it finds first name in table
print(soup.find('td', class_="hauptlink").text)

Kylian Mbappé


In [14]:
#testing it finds correct transfer value for first name in table
print(soup.find('td', class_="rechts hauptlink").text)

$176.00m 


In [15]:
print(soup.find('table', class_="items").find('img', class_='flaggenrahmen')['alt'])
#e['itemprop'] : e.text.strip() for e in soup.find_all(attrs={'itemprop':True})}                                            

France


In [16]:
#testing first page as a single dictionary
first_page_names = [name.text for name in soup.find_all('a', class_="spielprofil_tooltip tooltipstered")][:25]
first_page_values = [tf.text.replace('\xa0','') for tf in soup.find_all('td', class_="rechts hauptlink")]

first_page_nv = {}
for k,v in zip(first_page_names, first_page_values):
    first_page_nv[k] = v
first_page_nv

{'Kylian Mbappé': '$176.00m',
 'Erling Haaland': '$143.00m',
 'Harry Kane': '$132.00m',
 'Jadon Sancho': '$110.00m',
 'Mohamed Salah': '$110.00m',
 'Romelu Lukaku': '$110.00m',
 'Kevin De Bruyne': '$110.00m',
 'Neymar': '$110.00m',
 'Frenkie de Jong': '$99.00m',
 'Bruno Fernandes': '$99.00m',
 'Joshua Kimmich': '$99.00m',
 'Raheem Sterling': '$99.00m',
 'Marcus Rashford': '$93.50m',
 'Sadio Mané': '$93.50m',
 'Heung-min Son': '$93.50m',
 'Pedri': '$88.00m',
 'João Félix': '$88.00m',
 'Phil Foden': '$88.00m',
 'Lautaro Martínez': '$88.00m',
 'Marcos Llorente': '$88.00m',
 'Lionel Messi': '$88.00m',
 'Mason Mount': '$82.50m',
 'Matthijs de Ligt': '$82.50m',
 'Trent Alexander-Arnold': '$82.50m',
 'Rúben Dias': '$82.50m'}

In [71]:
#going to next page test, doesn't need to run in final
#var=2
#next_table = driver.find_element_by_xpath(f'//li[contains(@title, "Page {var}")]')

#next_table.click()


In [17]:
#put it all together

names = [name.text for name in soup.find('table', class_="items").find_all('a', class_="spielprofil_tooltip")]
values = [float(tf.text.replace('m\xa0','').replace('$', '').replace('.%0', '')) for tf \
                   in soup.find_all('td', class_="rechts hauptlink")]

for i in range(2,21):
    next_table = driver.find_element_by_xpath(f'//li[contains(@title, "Page {i}")]')
    next_table.click()
    
    time.sleep(3)
    
    soup2 = BeautifulSoup(driver.page_source, 'html.parser')
    
    names.extend([name.text for name in soup2.find('table', class_="items").\
                  find_all('a', class_="spielprofil_tooltip")])
    
    values.extend([float(tf.text.replace('m\xa0','').replace('$', '').replace('.%0', '')) for tf \
                   in soup2.find_all('td', class_="rechts hauptlink")])
    
    time.sleep(4)
    
   


In [18]:
nv_dict = {} 

for k,v in zip(names, values):
    nv_dict[k] = v

nv_dict

{'Kylian Mbappé': 176.0,
 'Erling Haaland': 143.0,
 'Harry Kane': 132.0,
 'Jadon Sancho': 110.0,
 'Mohamed Salah': 110.0,
 'Romelu Lukaku': 110.0,
 'Kevin De Bruyne': 110.0,
 'Neymar': 110.0,
 'Frenkie de Jong': 99.0,
 'Bruno Fernandes': 99.0,
 'Joshua Kimmich': 99.0,
 'Raheem Sterling': 99.0,
 'Marcus Rashford': 93.5,
 'Sadio Mané': 93.5,
 'Heung-min Son': 93.5,
 'Pedri': 88.0,
 'João Félix': 88.0,
 'Phil Foden': 88.0,
 'Lautaro Martínez': 88.0,
 'Marcos Llorente': 88.0,
 'Lionel Messi': 88.0,
 'Mason Mount': 82.5,
 'Matthijs de Ligt': 82.5,
 'Trent Alexander-Arnold': 82.5,
 'Rúben Dias': 82.5,
 'Marquinhos': 82.5,
 'Alphonso Davies': 77.0,
 'Declan Rice': 77.0,
 'Rodri': 77.0,
 'Mikel Oyarzabal': 77.0,
 'Federico Chiesa': 77.0,
 'Kai Havertz': 77.0,
 'Sergej Milinković-Savić': 77.0,
 'Bernardo Silva': 77.0,
 'Raphaël Varane': 77.0,
 'Serge Gnabry': 77.0,
 'Leon Goretzka': 77.0,
 'Jan Oblak': 77.0,
 'Casemiro': 77.0,
 'Bukayo Saka': 71.5,
 'Federico Valverde': 71.5,
 'Gianluigi Donnar

In [19]:
import pandas as pd
nv_dict = {'Name': names, 'Market Value (in millions USD)': values}
player_data = pd.DataFrame.from_dict(nv_dict)
player_data.head(20)

Name  Market Value (in millions USD)
0      Kylian Mbappé                           176.0
1     Erling Haaland                           143.0
2         Harry Kane                           132.0
3       Jadon Sancho                           110.0
4      Mohamed Salah                           110.0
5      Romelu Lukaku                           110.0
6    Kevin De Bruyne                           110.0
7             Neymar                           110.0
8    Frenkie de Jong                            99.0
9    Bruno Fernandes                            99.0
10    Joshua Kimmich                            99.0
11   Raheem Sterling                            99.0
12   Marcus Rashford                            93.5
13        Sadio Mané                            93.5
14     Heung-min Son                            93.5
15             Pedri                            88.0
16        João Félix                            88.0
17        Phil Foden                            88.0
18  Lautaro Martínez                            88.0
19   Marcos Llorente                            88.0

In [20]:
player_data.info

<bound method DataFrame.info of                Name  Market Value (in millions USD)
0     Kylian Mbappé                           176.0
1    Erling Haaland                           143.0
2        Harry Kane                           132.0
3      Jadon Sancho                           110.0
4     Mohamed Salah                           110.0
..              ...                             ...
495      Riqui Puig                            19.8
496         Éverton                            19.8
497    Daniel James                            19.8
498     Diego Rossi                            19.8
499      Tom Davies                            19.8

[500 rows x 2 columns]>

In [150]:
#player features
driver.get('https://fbref.com/en/comps/Big5/2020-2021/stats/players/2020-2021-Big-5-European-Leagues-Stats')

In [151]:
soup_features = BeautifulSoup(driver.page_source, 'html.parser')

In [ ]:
<tr data-row="0"><th scope="row" class="right " data-stat="ranker">1</th><td class="left " data-append-csv="Ismael-Aaneba" data-stat="player" csk="Aaneba, Ismael"><a href="/en/players/a7e4760c/Ismael-Aaneba">Ismael Aaneba</a></td><td class="left poptip" data-stat="nationality" data-tip="birth"><a href="/en/country/FRA/France-Football"><span style="white-space: nowrap"><span class="f-i f-fr" style="">fr</span> FRA</span></a></td><td class="center " data-stat="position" csk="3.3">FW,DF</td><td class="left " data-stat="squad"><a href="/en/squads/c0d3eab4/2020-2021/Strasbourg-Stats">Strasbourg</a></td><td class="left " data-stat="comp_level"><span title="France"><span class="f-i" style="background-image:url('https://d2p3bygnnzw9w3.cloudfront.net/req/202109021/flags/fr-2020.svg'); ">fr</span></span> <a href="/en/comps/13/10732/2020-2021-Ligue-1-Stats">Ligue 1</a></td><td class="center " data-stat="age">21</td><td class="center " data-stat="birth_year">1999</td><td class="right group_start" data-stat="games">2</td><td class="right iz" data-stat="games_starts">0</td><td class="right " data-stat="minutes" csk="11">11</td><td class="right " data-stat="minutes_90s">0.1</td><td class="right iz group_start" data-stat="goals">0</td><td class="right iz" data-stat="assists">0</td><td class="right iz" data-stat="goals_pens">0</td><td class="right iz" data-stat="pens_made">0</td><td class="right iz" data-stat="pens_att">0</td><td class="right iz" data-stat="cards_yellow">0</td><td class="right iz" data-stat="cards_red">0</td><td class="right non_qual iz group_start" data-stat="goals_per90">0.00</td><td class="right non_qual iz" data-stat="assists_per90">0.00</td><td class="right non_qual iz" data-stat="goals_assists_per90">0.00</td><td class="right non_qual iz" data-stat="goals_pens_per90">0.00</td><td class="right non_qual iz" data-stat="goals_assists_pens_per90">0.00</td><td class="right iz group_start" data-stat="xg">0.0</td><td class="right iz" data-stat="npxg">0.0</td><td class="right iz" data-stat="xa">0.0</td><td class="right iz" data-stat="npxg_xa">0.0</td><td class="right non_qual iz group_start" data-stat="xg_per90">0.00</td><td class="right non_qual iz" data-stat="xa_per90">0.00</td><td class="right non_qual iz" data-stat="xg_xa_per90">0.00</td><td class="right non_qual iz" data-stat="npxg_per90">0.00</td><td class="right non_qual iz" data-stat="npxg_xa_per90">0.00</td><td class="left group_start" data-stat="matches"><a href="/en/players/a7e4760c/matchlogs/2020-2021/summary/Ismael-Aaneba-Match-Logs">Matches</a></td></tr>
all_stats_standard

In [185]:
#testing to pull first name from table
print(soup_features.find('td', attrs={"data-stat": "player"}).text)

Ismael Aaneba


In [218]:
test_features = soup_features.find('table', id="stats_standard").find('tr', attrs={'data-row': '0'}).find_all(text=True)
test_features_labels = soup_features.find('table', id="stats_standard").find('thead').find_all(text=True)
test_features_labels_c = [e for e in test_features_labels if e != '\n']
test_features_labels_cc = test_features_labels_c[5:]
d = {k: v for k,v in zip(test_features_labels_cc, test_features)}
d

{'Rk': '1',
 'Player': 'Ismael Aaneba',
 'Nation': 'fr',
 'Pos': ' FRA',
 'Squad': 'FW,DF',
 'Comp': 'Strasbourg',
 'Age': 'fr',
 'Born': ' ',
 'MP': 'Ligue 1',
 'Starts': '21',
 'Min': '1999',
 '90s': '2',
 'Gls': '0',
 'Ast': '0',
 'G-PK': '0.00',
 'PK': '0',
 'PKatt': '0',
 'CrdY': '0',
 'CrdR': '0',
 'G+A': '0',
 'G+A-PK': '0.00',
 'xG': '0.0',
 'npxG': '0.00',
 'xA': '0.0',
 'npxG+xA': '0.00',
 'xG+xA': '0.0',
 'Matches': '0.00'}

In [21]:
import pandas as pd
#testing dataframe for all relevent info
test_df = pd.read_csv('data.txt', skiprows=5)
test_df.head()

Name  Nation   Pos                Comp  \
0              Ismael Aaneba\Ismael-Aaneba  fr FRA  FWDF          fr Ligue 1   
1  Patrick van Aanholt\Patrick-van-Aanholt  nl NED    DF  eng Premier League   
2                  Issah Abbas\Issah-Abbas  gh GHA  DFFW       de Bundesliga   
3        Yunis Abdelhamid\Yunis-Abdelhamid  ma MAR    DF          fr Ligue 1   
4              Sabit Abdulai\Sabit-Abdulai  gh GHA    MF          es La Liga   

    Age    MP  Starts     Min  Gls  Ast  ...   xG  npxG   xA  npxG+xA  xG.1  \
0  21.0   2.0     0.0    11.0  0.0  0.0  ...  0.0   0.0  0.0      0.0  0.00   
1  29.0  22.0    20.0  1777.0  0.0  1.0  ...  1.2   1.2  0.8      2.0  0.06   
2  21.0   2.0     0.0    18.0  0.0  0.0  ...  0.0   0.0  0.0      0.0  0.00   
3  32.0  33.0    33.0  2889.0  3.0  0.0  ...  1.7   1.7  0.3      1.9  0.05   
4  21.0   3.0     0.0    60.0  0.0  0.0  ...  0.0   0.0  0.0      0.0  0.00   

   xA.1  xG+xA  npxG.1  npxG+xA.1  Matches  
0  0.00   0.00    0.00       0.00  Matches  
1  0.04   0.10    0.06       0.10  Matches  
2  0.00   0.00    0.00       0.00  Matches  
3  0.01   0.06    0.05       0.06  Matches  
4  0.00   0.00    0.00       0.00  Matches  

[5 rows x 26 columns]

In [22]:
#cleaning data for name/nation/league
for i, name in enumerate(test_df['Name']):
    if '\\' in name:
        new_name = name.split('\\')
        final_name = new_name[0]
        test_df['Name'][i] = final_name
    else:
        continue

for i, nation in enumerate(test_df['Nation']):
    if " " in nation:
        new_nat = nation.split()
        final_nat = new_nat[1]
        test_df['Nation'][i] = final_nat 

for i, lea in enumerate(test_df['Comp']):
    if " " in lea:
        new_lea = lea.split(maxsplit=1)
        final_lea = new_lea[1]
        test_df['Comp'][i] = final_lea 
    
test_df.head()

/tmp/ipykernel_35950/3439706836.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df['Name'][i] = final_name
/tmp/ipykernel_35950/3439706836.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df['Nation'][i] = final_nat


TypeError: argument of type 'float' is not iterable

In [23]:
final_table = player_data.merge(test_df, on= 'Name')
final_table.head(50)

Name  Market Value (in millions USD) Nation   Pos  \
0             Kylian Mbappé                           176.0    FRA    FW   
1            Erling Haaland                           143.0    NOR    FW   
2                Harry Kane                           132.0    ENG    FW   
3              Jadon Sancho                           110.0    ENG  FWMF   
4             Mohamed Salah                           110.0    EGY    FW   
5             Romelu Lukaku                           110.0    BEL    FW   
6           Kevin De Bruyne                           110.0    BEL    MF   
7                    Neymar                           110.0    BRA  MFFW   
8           Frenkie de Jong                            99.0    NED  MFDF   
9           Bruno Fernandes                            99.0    POR    MF   
10           Joshua Kimmich                            99.0    GER    MF   
11          Raheem Sterling                            99.0    ENG    FW   
12          Marcus Rashford                            93.5    ENG    FW   
13               Sadio Mané                            93.5    SEN    FW   
14            Heung-min Son                            93.5    KOR    FW   
15                    Pedri                            88.0    ESP    MF   
16               João Félix                            88.0    POR  FWMF   
17               Phil Foden                            88.0    ENG  FWMF   
18         Lautaro Martínez                            88.0    ARG    FW   
19          Marcos Llorente                            88.0    ESP  MFDF   
20             Lionel Messi                            88.0    ARG  FWMF   
21              Mason Mount                            82.5    ENG  MFFW   
22         Matthijs de Ligt                            82.5    NED    DF   
23   Trent Alexander-Arnold                            82.5    ENG    DF   
24               Rúben Dias                            82.5    POR    DF   
25               Marquinhos                            82.5    BRA    DF   
26          Alphonso Davies                            77.0    CAN    DF   
27              Declan Rice                            77.0    ENG    MF   
28                    Rodri                            77.0    ESP    MF   
29          Mikel Oyarzabal                            77.0    ESP  FWMF   
30          Federico Chiesa                            77.0    ITA    DF   
31          Federico Chiesa                            77.0    ITA  MFDF   
32              Kai Havertz                            77.0    GER  MFFW   
33  Sergej Milinković-Savić                            77.0    SRB    MF   
34           Bernardo Silva                            77.0    POR  MFFW   
35           Raphaël Varane                            77.0    FRA    DF   
36             Serge Gnabry                            77.0    GER  FWMF   
37            Leon Goretzka                            77.0    GER    MF   
38                Jan Oblak                            77.0    SVN    GK   
39                 Casemiro                            77.0    BRA    MF   
40              Bukayo Saka                            71.5    ENG  FWDF   
41        Federico Valverde                            71.5    URU    MF   
42     Gianluigi Donnarumma                            71.5    ITA    GK   
43           Nicolò Barella                            71.5    ITA    MF   
44           Kingsley Coman                            71.5    FRA  FWMF   
45         Andrew Robertson                            71.5    SCO    DF   
46            Jack Grealish                            71.5    ENG  FWMF   
47              Timo Werner                            71.5    GER    FW   
48                Ansu Fati                            66.0    ESP    FW   
49             Jules Koundé                            66.0    FRA    DF   

                  Comp   Age    MP  Starts     Min   Gls  ...    xG  npxG  \
0           fr Ligue 1  21.0  31.0    27.0  2380.0  27.0  ...  24.6  

In [24]:
final_table.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 467 entries, 0 to 466
Data columns (total 27 columns):
 #   Column                          Non-Null Count  Dtype  
---  ------                          --------------  -----  
 0   Name                            467 non-null    object 
 1   Market Value (in millions USD)  467 non-null    float64
 2   Nation                          467 non-null    object 
 3   Pos                             467 non-null    object 
 4   Comp                            467 non-null    object 
 5   Age                             467 non-null    float64
 6   MP                              467 non-null    float64
 7   Starts                          467 non-null    float64
 8   Min                             467 non-null    float64
 9   Gls                             467 non-null    float64
 10  Ast                             467 non-null    float64
 11  G-PK                            467 non-null    float64
 12  Gls.1                           467 

In [25]:
#was at 99
no_info = []
for name in names:
    if name not in final_table['Name'].tolist():
        no_info.append(name)
no_info

['Nuno Mendes',
 'Nicolò Zaniolo',
 'Emiliano Buendía',
 'Ryan Gravenberch',
 'Bryan Gil',
 'Donyell Malen',
 'Nikola Vlasic',
 'André Onana',
 'Jesús Corona',
 'Ivan Toney',
 'David Neres',
 'Jérémy Doku',
 'Gabriel Barbosa',
 'Ilaix Moriba',
 'Antony',
 'Luis Díaz',
 'Dominik Szoboszlai',
 'Pedro Gonçalves',
 'Viktor Tsygankov',
 'Sardar Azmoun',
 'Rafa Silva',
 'Lisandro Martínez',
 'Max Aarons',
 'Ismaïla Sarr',
 'Patson Daka',
 'Noa Lang',
 'Todd Cantwell',
 'Malcom',
 'Alejandro Grimaldo',
 'Nicolás Tagliafico',
 'João Palhinha',
 'Thiago Almada',
 'Pedro Porro',
 'Darwin Núñez',
 'Karim Adeyemi',
 'Dodô',
 'Manor Solomon',
 'Gerson',
 'Paul Onuachu',
 'Julian Weigl',
 'Josko Gvardiol',
 'Marcos Senesi',
 'Ugurcan Cakir',
 'Khvicha Kvaratskhelia',
 'Wendel',
 'Cody Gakpo',
 'Nicolás De La Cruz',
 'Éverton',
 'Diego Rossi']

In [26]:
#searching for duplicates
duplicaterows = final_table[final_table.duplicated(subset = ['Name'])]
duplicaterows

Name  Market Value (in millions USD) Nation   Pos  \
31       Federico Chiesa                            77.0    ITA  MFDF   
123        Wesley Fofana                            44.0    FRA    DF   
136      Martin Ødegaard                            44.0    NOR  MFFW   
143        Thomas Partey                            44.0    GHA    MF   
172           Moise Kean                            38.5    ITA    FW   
252        Fikayo Tomori                            30.8    ENG    DF   
283        Edouard Mendy                            27.5    SEN    GK   
291           Ozan Kabak                            27.5    TUR    DF   
299           Ridle Baku                            27.5    GER    DF   
346  Jeff Reine-Adélaïde                            24.2    FRA    FW   
355     Joachim Andersen                            24.2    DEN    DF   
408       Diego Llorente                            22.0    ESP    DF   
412       Moussa Dembélé                            22.0    FRA  FWMF   
427         Ross Barkley                            22.0    ENG    MF   
445      Rayan Aït Nouri                            19.8    FRA    DF   
447          Amad Diallo                            19.8    CIV    MF   

                   Comp   Age    MP  Starts     Min   Gls  ...    xG  npxG  \
31           it Serie A  22.0  30.0    28.0  2210.0   8.0  ...   6.0   6.0   
123          fr Ligue 1  19.0   4.0     3.0   315.0   0.0  ...   0.2   0.2   
136          es La Liga  21.0   7.0     3.0   234.0   0.0  ...   0.1   0.1   
143          es La Liga  27.0   3.0     2.0   200.0   0.0  ...   0.1   0.1   
172          fr Ligue 1  20.0  26.0    22.0  1698.0  13.0  ...  10.7  10.7   
252          it Serie A  22.0  17.0    16.0  1466.0   1.0  ...   0.4   0.4   
283  eng Premier League  28.0  31.0    31.0  2745.0   0.0  ...   0.0   0.0   
291       de Bundesliga  20.0  14.0    14.0  1243.0   0.0  ...   1.0   1.0   
299       de Bundesliga  22.0   2.0     2.0   180.0   0.0  ...   0.0   0.0   
346          fr Ligue 1  22.0   1.0     0.0    24.0   0.0  ...   0.1   0.1   
355  eng Premier League  24.0  31.0    30.0  2730.0   1.0  ...   1.1   1.1   
408          es La Liga  26.0   1.0     1.0    90.0   0.0  ...   0.0   0.0   
412          es La Liga  24.0   5.0     0.0   100.0   0.0  ...   1.0   1.0   
427  eng Premier League  26.0   2.0     0.0    42.0   0.0  ...   0.0   0.0   
445  eng Premier League  19.0  21.0    16.0  1404.0   1.0  ...   0.6   0.6   
447          it Serie A  18.0   1.0     0.0    14.0   0.0  ...   0.0   0.0   

      xA  npxG+xA  xG.1  xA.1  xG+xA  npxG.1  npxG+xA.1  Matches  
31   6.5     12.5  0.24  0.26   0.51    0.24       0.51  Matches  
123  0.0      0.2  0.06  0.00   0.06    0.06       0.06  Matches  
136  0.4      0.5  0.04  0.15   0.19    0.04       0.19  Matches  
143  0.0      0.1  0.05  0.00   0.05    0.05       0.05  Matches  
172  0.9     11.6  0.57  0.05   0.61    0.57       0.61  Matches  
252  0.0      0.4  0.03  0.00   0.03    0.03       0.03  Matches  
283  0.0      0.0  0.00  0.00   0.00    0.00       0.00  Matches  
291  0.2      1.2  0.07  0.01   0.09    0.07       0.09  Matches  
299  0.0      0.0  0.00  0.00   0.00    0.00       0.00  Matches  
346  0.0      0.2  0.39  0.18   0.57    0.39       0.57  Matches  
355  0.5      1.6  0.04  0.02   0.05    0.04       0.05  Matches  
408  0.0      0.0  0.00  0.00   0.00    0.00       0.00  Matches  
412  0.0      1.1  0.92  0.02   0.95    0.92       0.95  Matches  
427  0.1      0.1  0.06  0.16   0.22    0.06       0.22  Matches  
445  1.0      1.6  0.04  0.06   0.10    0.04       0.10  Matches  
447  0.1      0.1  0.20  0.54   0.73    0.20       0.73  Matches  

[16 rows x 27 columns]

In [27]:
#duplicates because a player can be transefered mid season, therefore we are going to keep the second value, as their
#more recent play is a more likely indicator of value
final_table.drop_duplicates(subset=['Name'], keep='last', inplace=True)

In [43]:
import statsmodels.api as sm
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression, Lasso, LassoCV, Ridge, RidgeCV
from sklearn.metrics import r2_score

import matplotlib.pyplot as plt
import seaborn as sns
%config InlineBackend.figure_formats = ['svg']  # or svg
%matplotlib inline

sns.set(context='notebook', style='whitegrid', font_scale=1.2)

In [29]:
final_table.corr()

Market Value (in millions USD)       Age  \
Market Value (in millions USD)                        1.000000  0.003073   
Age                                                   0.003073  1.000000   
MP                                                    0.216922  0.109956   
Starts                                                0.240512  0.209888   
Min                                                   0.244170  0.201620   
Gls                                                   0.384246  0.225459   
Ast                                                   0.375612  0.163205   
G-PK                                                  0.370772  0.200163   
Gls.1                                                 0.304007  0.146974   
Ast.1                                                 0.270237  0.103325   
G+A                                                   0.342324  0.153404   
G-PK.1                                                0.275966  0.105428   
G+A-PK                                                0.324266  0.122985   
xG                                                    0.409938  0.197640   
npxG                                                  0.407388  0.163570   
xA                                                    0.370619  0.194191   
npxG+xA                                               0.441778  0.196842   
xG.1                                                  0.308245  0.111426   
xA.1                                                  0.242933  0.084876   
xG+xA                                                 0.328925  0.118785   
npxG.1                                                0.284416  0.060703   
npxG+xA.1                                             0.311252  0.081473   

                                      MP    Starts       Min       Gls  \
Market Value (in millions USD)  0.216922  0.240512  0.244170  0.384246   
Age                             0.109956  0.209888  0.201620  0.225459   
MP                              1.000000  0.868523  0.879076  0.315162   
Starts                          0.868523  1.000000  0.990750  0.246627   
Min                             0.879076  0.990750  1.000000  0.235799   
Gls                             0.315162  0.246627  0.235799  1.000000   
Ast                             0.373136  0.306789  0.287025  0.532759   
G-PK                            0.316610  0.227863  0.216763  0.968621   
Gls.1                           0.129566 -0.010938 -0.019326  0.907015   
Ast.1                           0.171474  0.021758  0.005188  0.408604   
G+A                             0.169081  0.000396 -0.012713  0.851878   
G-PK.1                          0.110444 -0.053815 -0.061447  0.845263   
G+A-PK                          0.158375 -0.029329 -0.042342  0.795910   
xG                              0.330037  0.261847  0.250460  0.957500   
npxG                            0.338639  0.248705  0.237144  0.928702   
xA                              0.399614  0.312542  0.294478  0.555093   
npxG+xA                         0.406476  0.306616  0.290945  0.886672   
xG.1                            0.064176 -0.063284 -0.072171  0.836288   
xA.1                            0.070162 -0.089150 -0.105964  0.399328   
xG+xA                           0.075755 -0.083538 -0.096816  0.791249   
npxG.1                          0.034747 -0.116397 -0.124322  0.772406   
npxG+xA.1                       0.055762 -0.123516 -0.136727  0.734291   

                                     Ast      G-PK     Gls.1     Ast.1  ...  \
Market Value (in millions USD)  0.375612  0.370772  0.304007  0.270237  ...   
Age                             0.163205  0.200163  0.146974  0.103325  ...   
MP                              0.373136  0.316610  0.129566  0.171474  ...   
Starts                          0.306789  0.227863 -0.010938  0.021758  ...   
Min                             0.287025  0.216763 -0.019326  0.005188  ...   
Gls                             0.532759  0.968621  0.907015  0.408604  ...   
Ast                        

In [140]:
paired_down_ft = final_table.drop(columns=['Name', 'Matches','MP', 'Starts', 'G-PK','Gls.1','Ast.1','G-PK.1','npxG', 'G+A-PK', 'xA.1', 'npxG.1', 'npxG+xA.1'])

In [165]:
sns.pairplot(paired_down_ft, height = 1.5)

In [31]:
lr = LinearRegression()
select_columns = ['Age', 'Min', 'Gls', 'Ast', 'G+A', 'xG', 'xA', 'npxG+xA', 'xG.1', 'xG+xA']
X = final_table.loc[:,select_columns]
y = final_table['Market Value (in millions USD)']
lr.fit(X, y)
lr.score(X, y)

0.22971969264891734

In [ ]:
split_and_validate(, y)

In [35]:
def split_and_validate(X, y):
  
    X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=13)
    
    lr.fit(X_train, y_train)
    
    val_score = lr.score(X_val, y_val)
    
    print('\nValidation R^2 score was:', val_score)
    print('Feature coefficient results: \n')
    for feature, coef in zip(X.columns, lr.coef_):
        print(feature, ':', f'{coef:.2f}') 
        

In [34]:
split_and_validate(X, y)


Validation R^2 score was: 0.24914351200502327
Feature coefficient results: 

Age : -0.68
Min : 0.00
Gls : -0.23
Ast : 0.19
G+A : 3.91
xG : 1.02
xA : 1.99
npxG+xA : 0.40
xG.1 : 6.39
xG+xA : -18.60


In [175]:
X.columns

Index(['Comp', 'Age', 'Min', 'Gls', 'Ast', 'G+A', 'xG', 'xA', 'npxG+xA',
       'xG.1', 'xG+xA'],
      dtype='object')

In [41]:
X2 = X.join(final_table.loc[:,['Pos', 'Comp']])
X2.head()

Age     Min   Gls   Ast   G+A    xG   xA  npxG+xA  xG.1  xG+xA   Pos  \
0  21.0  2380.0  27.0   7.0  1.29  24.6  4.6     24.7  0.93   1.11    FW   
1  20.0  2407.0  27.0   6.0  1.23  23.7  5.4     25.9  0.89   1.09    FW   
2  27.0  3082.0  23.0  14.0  1.08  20.5  7.4     24.8  0.60   0.81    FW   
3  20.0  2062.0   8.0  11.0  0.83   7.4  6.8     13.4  0.32   0.62  FWMF   
4  28.0  3078.0  22.0   5.0  0.79  20.9  6.3     22.6  0.61   0.79    FW   

                 Comp  
0          fr Ligue 1  
1       de Bundesliga  
2  eng Premier League  
3       de Bundesliga  
4  eng Premier League

In [42]:
split_and_validate(pd.get_dummies(X2, drop_first=True), y)


Validation R^2 score was: 0.27098522060296437
Feature coefficient results: 

Age : -1.01
Min : -0.00
Gls : -0.69
Ast : -0.33
G+A : 15.84
xG : 0.75
xA : 0.98
npxG+xA : 1.73
xG.1 : 5.47
xG+xA : -9.08
Pos_DFFW : -3.59
Pos_DFMF : 6.94
Pos_FW : -16.56
Pos_FWDF : -15.17
Pos_FWMF : -14.17
Pos_GK : 8.46
Pos_MF : -0.99
Pos_MFDF : 3.24
Pos_MFFW : -11.94
Comp_eng Premier League : 5.43
Comp_es La Liga : 5.99
Comp_fr Ligue 1 : -3.97
Comp_it Serie A : 0.93


In [45]:
X3 = final_table.drop(columns=['Market Value (in millions USD)','Nation','Name','Matches'])
X3.head()

Pos                Comp   Age    MP  Starts     Min   Gls   Ast  G-PK  \
0    FW          fr Ligue 1  21.0  31.0    27.0  2380.0  27.0   7.0  21.0   
1    FW       de Bundesliga  20.0  28.0    27.0  2407.0  27.0   6.0  25.0   
2    FW  eng Premier League  27.0  35.0    35.0  3082.0  23.0  14.0  19.0   
3  FWMF       de Bundesliga  20.0  26.0    24.0  2062.0   8.0  11.0   7.0   
4    FW  eng Premier League  28.0  37.0    34.0  3078.0  22.0   5.0  16.0   

   Gls.1  ...  G+A-PK    xG  npxG   xA  npxG+xA  xG.1  xA.1  xG+xA  npxG.1  \
0   1.02  ...    1.06  24.6  20.1  4.6     24.7  0.93  0.17   1.11    0.76   
1   1.01  ...    1.16  23.7  20.5  5.4     25.9  0.89  0.20   1.09    0.77   
2   0.67  ...    0.96  20.5  17.5  7.4     24.8  0.60  0.22   0.81    0.51   
3   0.35  ...    0.79   7.4   6.6  6.8     13.4  0.32  0.30   0.62    0.29   
4   0.64  ...    0.61  20.9  16.4  6.3     22.6  0.61  0.18   0.79    0.48   

   npxG+xA.1  
0       0.93  
1       0.97  
2       0.73  
3       0.58  
4       0.66  

[5 rows x 23 columns]

In [46]:
split_and_validate(pd.get_dummies(X3, drop_first=True), y)


Validation R^2 score was: 0.2736308444511151
Feature coefficient results: 

Age : -1.02
MP : -0.80
Starts : -1.18
Min : 0.02
Gls : 10.28
Ast : 0.03
G-PK : -11.60
Gls.1 : 132.91
Ast.1 : -16.57
G+A : -437.16
G-PK.1 : -129.27
G+A-PK : 462.68
xG : -7.74
npxG : 25.23
xA : 17.07
npxG+xA : -14.71
xG.1 : 187.91
xA.1 : 218.45
xG+xA : 45.81
npxG.1 : 28.39
npxG+xA.1 : -266.29
Pos_DFFW : -4.21
Pos_DFMF : 8.59
Pos_FW : -13.73
Pos_FWDF : -5.51
Pos_FWMF : -10.51
Pos_GK : 6.96
Pos_MF : 1.44
Pos_MFDF : 3.99
Pos_MFFW : -7.88
Comp_eng Premier League : 4.92
Comp_es La Liga : 6.42
Comp_fr Ligue 1 : -1.74
Comp_it Serie A : 2.37


In [48]:
def lasso_split_and_validate(X, y, a):
    
    lasso_model = Lasso(alpha = a)
    
    X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=13)
    
    lasso_model.fit(X_train, y_train)
    
    val_score = lasso_model.score(X_val, y_val)
    
    print('\nValidation R^2 score was:', val_score)
    print('Feature coefficient results: \n')
    for feature, coef in zip(X.columns, lr.coef_):
        print(feature, ':', f'{coef:.2f}') 
        

In [ ]:
#lasso_model = Lasso(alpha = .1) # this is a VERY HIGH regularization strength!, wouldn't usually be used
#asso_model.fit(X_train.loc[:,selected_columns], y_train)

In [62]:
lasso_split_and_validate(pd.get_dummies(X3, drop_first=True), y, .12) 


Validation R^2 score was: 0.28958847709166446
Feature coefficient results: 

Age : -1.02
MP : -0.80
Starts : -1.18
Min : 0.02
Gls : 10.28
Ast : 0.03
G-PK : -11.60
Gls.1 : 132.91
Ast.1 : -16.57
G+A : -437.16
G-PK.1 : -129.27
G+A-PK : 462.68
xG : -7.74
npxG : 25.23
xA : 17.07
npxG+xA : -14.71
xG.1 : 187.91
xA.1 : 218.45
xG+xA : 45.81
npxG.1 : 28.39
npxG+xA.1 : -266.29
Pos_DFFW : -4.21
Pos_DFMF : 8.59
Pos_FW : -13.73
Pos_FWDF : -5.51
Pos_FWMF : -10.51
Pos_GK : 6.96
Pos_MF : 1.44
Pos_MFDF : 3.99
Pos_MFFW : -7.88
Comp_eng Premier League : 4.92
Comp_es La Liga : 6.42
Comp_fr Ligue 1 : -1.74
Comp_it Serie A : 2.37
